In [ ]:
!pip install -q stanza transformers sentencepiece torch sentence-transformers arabert pyarabic yake bert-score python-bidi

In [ ]:
import re
import difflib
import numpy as np
import torch
import pyarabic.araby as araby
import stanza
from transformers import AutoTokenizer, AutoModel
from sentence_transformers import SentenceTransformer, util
import arabert.preprocess
import yake
from bert_score import score as bertscore
from sentence_transformers import util

torch.set_grad_enabled(False)

ARAELECTRA_NAME = "aubmindlab/araelectra-base-discriminator"
SBERT_MODEL      = "sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2"
QG_MODEL         = "Mihakram/AraT5-base-question-generation"
print("ARAELECTRA_NAME:", ARAELECTRA_NAME)
print("SBERT_MODEL:", SBERT_MODEL)
print("QG_MODEL:", QG_MODEL)


In [ ]:
stanza.download('ar')
nlp = stanza.Pipeline(lang='ar', processors='tokenize,pos,lemma,depparse', tokenize_no_ssplit=False)
arabert_prep = arabert.preprocess.ArabertPreprocessor(ARAELECTRA_NAME)

tokenizer_electra = AutoTokenizer.from_pretrained(ARAELECTRA_NAME)
model_electra     = AutoModel.from_pretrained(ARAELECTRA_NAME)

sbert = SentenceTransformer(SBERT_MODEL)

from transformers import AutoTokenizer as HFTokenizer, AutoModelForSeq2SeqLM
qg_tokenizer = HFTokenizer.from_pretrained(QG_MODEL)
qg_model     = AutoModelForSeq2SeqLM.from_pretrained(QG_MODEL)

device = "cuda" if torch.cuda.is_available() else "cpu"
qg_model = qg_model.to(device)

INFO:stanza:Downloaded file to /root/stanza_resources/resources.json
INFO:stanza:Downloading default packages for language: ar (Arabic) ...


INFO:stanza:Downloaded file to /root/stanza_resources/ar/default.zip
INFO:stanza:Finished downloading models and saved to /root/stanza_resources
INFO:stanza:Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


INFO:stanza:Downloaded file to /root/stanza_resources/resources.json


In [33]:
# text = """المحور العصبي هو نتوء طويل ونحيل، يحمل النبضات الكهربائية بعيدًا عن جسم الخلية إلى الخلايا العصبية الأخرى، أو العضلات، أو الغدد.
# يُغطى العديد من المحاور العصبية بمادة دهنية تُسمى غمد الميالين، والتي تعمل كعازل وتُسرّع من نقل الإشارات.
# ينتهي المحور العصبي عند نهايات المحور العصبي، حيث يتم إطلاق النواقل العصبية للتواصل مع الخلايا العصبية الأخرى، أو الخلايا المستهدفة."""
# text = """الجهاز العصبي المركزي:
# كثُر في الآونة الأخيرة انتشار حالات السكتة الدماغية، وهي حالة تحدث نتيجة عدم وصول الدم المحمّل بالأكسجين إلى الدماغ؛ كحالة طبية طارئة تبدأ فيها خلايا الدماغ بالموت بعد بضع دقائق من عدم وصول الأكسجين. وهناك نوعان رئيسان من السكتة هما السكتة الدماغية التي تحدث بسبب الجلطات الدموية، وتشكل
# 87% من الحالات، والسكتة الدماغية التي تحدث بسبب النزيف في الدماغ أو حوله.
# وتختلف أعراضها، إذ تشمل: الخدر المفاجئ، وعدم القدرة على تحريك الوجه أو الذراع أو الساق (لاسيما في أحد جانبي الجسم)، والارتباك، ومشاكل في التحدث والرؤية والدوخة، وصعوبة في المشي، وفقدان التوازن، والصداع المفاجئ والشديد، ومشاكل في التنفس، وفقدان الوعي."""
text = "يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءاً من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان"
print("The Original:\n", text)


The Original:
 يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءاً من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان


In [34]:
def normalize(s: str) -> str:
    t = araby.strip_tashkeel(s)
    t = t.replace('آ','ا').replace('أ','ا').replace('إ','ا').replace('ى','ي')
    t = t.replace('ـ','')
    t = ' '.join(t.split())
    return t
text_norm = normalize(text)
print("Text after normalization:\n", text_norm)

Text after normalization:
 يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان


In [35]:
def build_char_map(src: str, tgt: str):
    sm = difflib.SequenceMatcher(a=src, b=tgt)
    src2tgt = [-1] * len(src)
    for tag, i1, i2, j1, j2 in sm.get_opcodes():
        if tag == 'equal':
            for k in range(i2 - i1):
                src2tgt[i1 + k] = j1 + k
        elif tag in ('replace', 'delete'):
            for k in range(i2 - i1):
                src2tgt[i1 + k] = j1
        elif tag == 'insert':
            pass
    last = 0
    for i in range(len(src2tgt)):
        if src2tgt[i] == -1:
            src2tgt[i] = last
        else:
            last = src2tgt[i]
    return src2tgt

def map_span_src_to_tgt(src2tgt, start, end, tgt_len):
    if start >= len(src2tgt): start = max(0, len(src2tgt)-1)
    if end == 0: end = 1
    if end-1 >= len(src2tgt): end = len(src2tgt)
    ts = src2tgt[start]
    te = src2tgt[end-1] + 1
    ts = max(0, min(ts, max(0, tgt_len-1)))
    te = max(ts+1, min(te, tgt_len))
    return ts, te

def token_indices_overlapping_span(offsets, span_start, span_end):
    idxs = []
    for i, (s, e) in enumerate(offsets):
        if e > span_start and s < span_end:
            idxs.append(i)
    return idxs

def electra_hidden_states(prep_text):
    encoded = tokenizer_electra(prep_text, return_tensors="pt", return_offsets_mapping=True, padding=False, truncation=True)
    offsets = encoded.pop('offset_mapping')[0].tolist()
    with torch.no_grad():
        out = model_electra(**encoded)
    H = out.last_hidden_state.squeeze(0)
    return offsets, H

def word_span_list_from_stanza(doc):
    spans = []
    for si, sent in enumerate(doc.sentences):
        for ti, tok in enumerate(sent.tokens):
            for w in tok.words:
                spans.append({
                    "text": w.text,
                    "start": tok.start_char,
                    "end": tok.end_char,
                    "upos": w.upos,
                    "feats": getattr(w, "feats", None),
                    "deprel": w.deprel,
                    "head": w.head,
                    "sent_idx": si,
                    "tok_idx": ti
                })
    return spans

def electra_phrase_vec_via_offsets(span_start, span_end, src2tgt, prep_text, offsets, H):
    ts, te = map_span_src_to_tgt(src2tgt, span_start, span_end, len(prep_text))
    tok_ids = token_indices_overlapping_span(offsets, ts, te)
    if not tok_ids:
        return None
    vecs = [H[i] for i in tok_ids]
    return torch.stack(vecs, dim=0).mean(dim=0)


In [36]:
doc = nlp(text_norm)
for si, sentence in enumerate(doc.sentences, start=1):
    print(f"\n=== Sentence {si} ===")
    for w in sentence.words:
        feats = w.feats if w.feats else "_"
        head_text = sentence.words[w.head-1].text if w.head and w.head-1 < len(sentence.words) else "ROOT"
        print(f"Word: {w.text:<15} UPOS: {w.upos:<6} Dep: {w.deprel:<9} Head: {head_text:<12} Feats: {feats}")


=== Sentence 1 ===
Word: يتشكل           UPOS: VERB   Dep: root      Head: ROOT         Feats: Aspect=Imp|Gender=Masc|Mood=Ind|Number=Sing|Person=3|VerbForm=Fin|Voice=Act
Word: الماضي          UPOS: ADJ    Dep: nsubj     Head: يتشكل        Feats: Case=Nom|Definite=Def|Gender=Masc|Number=Sing
Word: غمد             UPOS: NOUN   Dep: nsubj     Head: يتشكل        Feats: Case=Nom|Definite=Cons|Number=Sing
Word: النخاعين        UPOS: NOUN   Dep: nmod      Head: غمد          Feats: Case=Gen|Definite=Def|Number=Dual
Word: في              UPOS: ADP    Dep: case      Head: الجهاز       Feats: AdpType=Prep
Word: الجهاز          UPOS: NOUN   Dep: nmod      Head: غمد          Feats: Case=Gen|Definite=Def|Number=Sing
Word: العصبي          UPOS: ADJ    Dep: amod      Head: الجهاز       Feats: Case=Gen|Definite=Def|Gender=Masc|Number=Sing
Word: المركزي         UPOS: ADJ    Dep: amod      Head: الجهاز       Feats: Case=Gen|Definite=Def|Gender=Masc|Number=Sing
Word: بدءا            UPOS: NOUN   Dep: ob

In [37]:
def build_noun_phrases(doc, text_norm):
    noun_phrases = []
    for si, sent in enumerate(doc.sentences):
        words_info = []
        for ti, tok in enumerate(sent.tokens):
            for w in tok.words:
                words_info.append({
                    "id": w.id,
                    "text": w.text,
                    "upos": w.upos,
                    "deprel": w.deprel,
                    "head": w.head,
                    "start": tok.start_char,
                    "end": tok.end_char,
                    "tok_idx": ti
                })
        id2info = {wi["id"]: wi for wi in words_info}

        for wi in words_info:
            if wi["upos"] not in {"NOUN","PROPN"}:
                continue
            head = wi
            left_mods, right_mods = [], []
            for cj in words_info:
                if cj["head"] == head["id"] and cj["deprel"] in {"amod","compound","nmod"}:
                    if cj["start"] <= head["start"]:
                        left_mods.append(cj)
                    else:
                        right_mods.append(cj)
            left_mods  = sorted(left_mods,  key=lambda x: x["start"])
            right_mods = sorted(right_mods, key=lambda x: x["start"])
            phrase_tokens = left_mods + [head] + right_mods
            if not phrase_tokens:
                continue
            if len(phrase_tokens) < 2 and head["upos"] != "PROPN":
                continue
            span_start = min(t["start"] for t in phrase_tokens)
            span_end   = max(t["end"]   for t in phrase_tokens)
            phrase_text = text_norm[span_start:span_end].strip()
            phrase_text = re.sub(r"\s+"," ", phrase_text)
            if len(phrase_text) < 2:
                continue
            noun_phrases.append({
                "text": phrase_text,
                "start": span_start,
                "end": span_end,
                "head_text": head["text"],
                "sent_idx": si,
                "token_indices": [t["tok_idx"] for t in phrase_tokens]
            })
    uniq = {}
    for np_item in noun_phrases:
        key = np_item["text"]
        if key not in uniq or (np_item["end"] - np_item["start"]) > (uniq[key]["end"] - uniq[key]["start"]):
            uniq[key] = np_item
    return list(uniq.values())

nps = build_noun_phrases(doc, text_norm)
print("Number of nominal phrases :", len(nps))
for i, p in enumerate(nps[:20], 1):
    print(f"{i:>2}. {p['text']}  (span={p['start']}:{p['end']}, head={p['head_text']})")

Number of nominal phrases : 6
 1. غمد النخاعين في الجهاز  (span=6:28, head=غمد)
 2. الجهاز العصبي المركزي  (span=22:43, head=الجهاز)
 3. بدءا من خلايا  (span=44:57, head=بدءا)
 4. خلايا الدبق  (span=52:63, head=خلايا)
 5. الدبق قليلة  (span=58:69, head=الدبق)
 6. الجهاز العصبي المحيطي  (span=85:106, head=الجهاز)


In [38]:
def mmr_select(doc_emb, cand_embs, candidates, k=10, lam=0.7):
    if len(candidates) == 0: return []
    chosen_idx, cand_idx = [], list(range(len(candidates)))
    sim_doc = util.cos_sim(doc_emb, cand_embs)[0]
    first = int(np.argmax(sim_doc.cpu().numpy()))
    chosen_idx.append(first); cand_idx.remove(first)
    if len(candidates) == 1 or k == 1:
        return [candidates[first]]
    sim_between = util.cos_sim(cand_embs, cand_embs)
    for _ in range(min(k, len(candidates)) - 1):
        best_i, best_score = None, -1e9
        for i in cand_idx:
            redundancy = max(sim_between[i, j].item() for j in chosen_idx) if chosen_idx else 0.0
            score = lam*sim_doc[i].item() - (1-lam)*redundancy
            if score > best_score:
                best_score, best_i = score, i
        chosen_idx.append(best_i); cand_idx.remove(best_i)
    return [candidates[i] for i in chosen_idx]

def rank_keyphrases_with_mmr(text_norm, nps, arabert_prep, sbert, TOP_K=12, alpha=0.8, lam=0.7):
    if not nps: return [], []
    phrases = [p["text"] for p in nps]
    text_prep = arabert_prep.preprocess(text_norm)
    src2tgt = build_char_map(text_norm, text_prep)
    # sBERT
    doc_emb_sbert  = sbert.encode([text_prep], convert_to_tensor=True)
    phr_embs_sbert = sbert.encode(phrases, convert_to_tensor=True)
    sims_sbert = util.cos_sim(doc_emb_sbert, phr_embs_sbert).cpu().numpy()[0]
    # ELECTRA doc vec
    prep_offsets, prep_H = electra_hidden_states(text_prep)
    with torch.no_grad():
        doc_vec_electra = prep_H.mean(dim=0)
    # ELECTRA phrase sims via span
    sims_electra = []
    for p in nps:
        v = electra_phrase_vec_via_offsets(p["start"], p["end"], src2tgt, text_prep, prep_offsets, prep_H)
        if v is None:
            sims_electra.append(0.0)
        else:
            num = torch.dot(doc_vec_electra, v).item()
            den = (doc_vec_electra.norm().item() * v.norm().item() + 1e-9)
            sims_electra.append(num/den)
    sims_electra = np.array(sims_electra)
    final_scores = alpha * sims_sbert + (1 - alpha) * sims_electra
    order = np.argsort(-final_scores)
    ranked = [(phrases[i], float(final_scores[i]), float(sims_sbert[i]), float(sims_electra[i])) for i in order]
    top_diverse = mmr_select(doc_emb_sbert, phr_embs_sbert, phrases, k=min(TOP_K, len(phrases)), lam=lam)
    return ranked, top_diverse

ranked, top_diverse = rank_keyphrases_with_mmr(text_norm, nps, arabert_prep, sbert, TOP_K=12, alpha=0.8, lam=0.7)
print("MMR selection (various):", top_diverse[:10])

print("\nTop 15 by blended (phrase, blended, sBERT, ELECTRA_ctx):")
for phr, sc, sb, el in ranked[:15]:
    print(f"{phr:<40s} -> {sc:.4f} | sBERT={sb:.4f} | ELECTRA={el:.4f}")


MMR selection (various): ['الجهاز العصبي المركزي', 'الجهاز العصبي المحيطي', 'بدءا من خلايا', 'خلايا الدبق', 'غمد النخاعين في الجهاز', 'الدبق قليلة']

Top 15 by blended (phrase, blended, sBERT, ELECTRA_ctx):
الجهاز العصبي المركزي                    -> 0.8126 | sBERT=0.7804 | ELECTRA=0.9415
الجهاز العصبي المحيطي                    -> 0.7930 | sBERT=0.7494 | ELECTRA=0.9674
خلايا الدبق                              -> 0.6421 | sBERT=0.5611 | ELECTRA=0.9663
بدءا من خلايا                            -> 0.6291 | sBERT=0.5483 | ELECTRA=0.9524
الدبق قليلة                              -> 0.3127 | sBERT=0.1528 | ELECTRA=0.9525
غمد النخاعين في الجهاز                   -> 0.2822 | sBERT=0.1064 | ELECTRA=0.9855


In [39]:
def yake_scores_for_phrases(text_norm, phrases, max_ngram_size=5, lan='ar'):
    kw_extractor = yake.KeywordExtractor(lan=lan, n=max_ngram_size, dedupLim=0.9, top=1000)
    scored = kw_extractor.extract_keywords(text_norm)
    norm = lambda s: re.sub(r"\s+"," ", s).strip().lower()
    scored_norm = {norm(k): v for k, v in scored}
    score_map = {}
    for p in phrases:
        pn = norm(p)
        score_map[p] = scored_norm.get(pn, None)
    return score_map

def invert_and_minmax_yake(score_map):
    vals = []
    for v in score_map.values():
        vals.append(None if v is None else 1.0/(1.0+v))
    finite_vals = [x for x in vals if x is not None]
    if not finite_vals:
        return {k: 0.0 for k in score_map.keys()}
    vmin, vmax = min(finite_vals), max(finite_vals)
    rng = (vmax - vmin) if vmax > vmin else 1.0
    out = {}
    for (k, v), pos in zip(score_map.items(), vals):
        out[k] = 0.0 if pos is None else (pos - vmin)/rng
    return out

def blend_semantic_with_yake(ranked_semantic, yake_norm_map, w_sem=0.7, w_yake=0.3):
    merged = []
    for phr, sem_sc, sb, el in ranked_semantic:
        y = yake_norm_map.get(phr, 0.0)
        final = w_sem*sem_sc + w_yake*y
        merged.append((phr, final, sem_sc, y, sb, el))
    merged.sort(key=lambda x: -x[1])
    return merged

phrases = [r[0] for r in ranked]
yake_raw  = yake_scores_for_phrases(text_norm, phrases, max_ngram_size=5, lan='ar')
yake_norm = invert_and_minmax_yake(yake_raw)

ranked_blended = blend_semantic_with_yake(ranked, yake_norm, w_sem=0.7, w_yake=0.3)

print("Top 15 (Blended SEM+YAKE):")
for phr, final, sem_sc, yake_sc, sb, el in ranked_blended[:15]:
    print(f"{phr:<40s} -> final={final:.4f} | sem={sem_sc:.4f} | yake={yake_sc:.4f} | sBERT={sb:.4f} | ELECTRA={el:.4f}")


Top 15 (Blended SEM+YAKE):
الجهاز العصبي المركزي                    -> final=0.8688 | sem=0.8126 | yake=1.0000 | sBERT=0.7804 | ELECTRA=0.9415
الجهاز العصبي المحيطي                    -> final=0.8551 | sem=0.7930 | yake=1.0000 | sBERT=0.7494 | ELECTRA=0.9674
خلايا الدبق                              -> final=0.4495 | sem=0.6421 | yake=0.0000 | sBERT=0.5611 | ELECTRA=0.9663
بدءا من خلايا                            -> final=0.4404 | sem=0.6291 | yake=0.0000 | sBERT=0.5483 | ELECTRA=0.9524
غمد النخاعين في الجهاز                   -> final=0.4177 | sem=0.2822 | yake=0.7339 | sBERT=0.1064 | ELECTRA=0.9855
الدبق قليلة                              -> final=0.2565 | sem=0.3127 | yake=0.1254 | sBERT=0.1528 | ELECTRA=0.9525


In [40]:
def split_by_dots(text: str):
    parts = re.split(r"\.{1,}\s*", text)
    sentences = [p.strip() for p in parts if p.strip()]
    return sentences

def sentence_kind_from_root(stanza_sentence):
    root = next((w for w in stanza_sentence.words if w.deprel == "root"), None)
    if not root:
        return "unknown"
    return "verbal" if root.upos == "VERB" else "nominal"

def split_and_tag_nominal_verbal_by_dots(text_norm, nlp):
    sents = split_by_dots(text_norm)
    tagged = []
    for s in sents:
        doc_s = nlp(s)
        if not doc_s.sentences:
            tagged.append({"text": s, "kind": "unknown"})
            continue
        kind = sentence_kind_from_root(doc_s.sentences[0])
        tagged.append({"text": s, "kind": kind})
    return tagged
def link_phrases_to_sentences_by_dots(text_norm, phrases, nlp, sbert, top_k_per_phrase=2):
    sentences_tagged = split_and_tag_nominal_verbal_by_dots(text_norm, nlp)
    if not sentences_tagged:
        return [], {p: [] for p in phrases}

    sent_texts = [m["text"] for m in sentences_tagged]
    sent_embs  = sbert.encode(sent_texts, convert_to_tensor=True)

    phrase_links = {}
    for p in phrases:
        p_emb = sbert.encode([p], convert_to_tensor=True)
        sims = util.cos_sim(p_emb, sent_embs)[0].cpu().numpy()
        order = np.argsort(-sims)
        links = []
        for idx in order[:min(top_k_per_phrase, len(order))]:
            links.append({
                "sent": sent_texts[idx],
                "sim": float(sims[idx]),
                "kind": sentences_tagged[idx]["kind"]
            })
        phrase_links[p] = links

    return sentences_tagged, phrase_links


tagged_sents = split_and_tag_nominal_verbal_by_dots(text_norm, nlp)

print("\nSentences (divided by points only) and their classification:")
for i, it in enumerate(tagged_sents, 1):
    print(f"{i:>2}. ({it['kind']}) {it['text']}")

topK_for_support = 1
phr_top = [x[0] for x in ranked_blended[:5]]
sentences_tagged, phrase_links = link_phrases_to_sentences_by_dots(
    text_norm, phr_top, nlp, sbert, top_k_per_phrase=topK_for_support
)

print("\nLinking phrases to supporting sentences (highest similarity):")
for p in phr_top:
    print(f"- عبارة: {p}")
    for l in phrase_links.get(p, []):
        print(f"   • ({l['kind']}) sim={l['sim']:.3f} | {l['sent']}")


Sentences (divided by points only) and their classification:
 1. (verbal) يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان

Linking phrases to supporting sentences (highest similarity):
- عبارة: الجهاز العصبي المركزي
   • (verbal) sim=0.780 | يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
- عبارة: الجهاز العصبي المحيطي
   • (verbal) sim=0.749 | يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
- عبارة: خلايا الدبق
   • (verbal) sim=0.561 | يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
- عبارة: بدءا من خلايا
   • (verbal) sim=0.548 | يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
- عبارة: غمد النخاعين في الجهاز
   • (verbal) s

In [42]:
def gen_unified_question_freeform(phrases, supports, context_text, max_len=96, num_beams=5):
    context_short = context_text.strip()[:600]
    items_block = "\n".join(
        [f"- العبارة: {p}\n  جملة داعمة: {s}" for p, s in zip(phrases, supports)]
    )
    prompt = (
        "حوّل العبارات التالية إلى سؤال واحد شامل بالعربية يعتمد على السياق. "
        "يجب أن يغطي جميع العبارات بشكل موجز وواضح.\n"
        f"{items_block}\n"
        f"سياق: {context_short}\n"
        "السؤال الموحد:"
    )

    inputs = qg_tokenizer(prompt, return_tensors="pt", truncation=True).to(device)
    outputs = qg_model.generate(
        **inputs,
        max_length=max_len,
        num_beams=num_beams,
        early_stopping=True,
        no_repeat_ngram_size=3
    )
    q = qg_tokenizer.decode(outputs[0], skip_special_tokens=True).strip()
    q = q.rstrip("?.؟")
    if q and not q.endswith("؟"):
        q += "؟"
    return q

def unified_question_from_top5_phrases(text_norm, ranked_blended, nlp, sbert, top_k=5):
    if not ranked_blended:
        print("لا توجد عبارات.")
        return {"phrases": [], "supports": [], "question": ""}
    top_n = min(top_k, len(ranked_blended))
    phrases = [ranked_blended[i][0] for i in range(top_n)]

    supports = []
    for p in phrases:
        s = best_support_sentence_by_dots(text_norm, p, nlp, sbert)
        supports.append(s)

    unified_q = gen_unified_question_freeform(phrases, supports, context_text=text_norm)
    print("The context : :\n", text_norm, "\n")
    print("The selected phrase (Top):")
    for i, p in enumerate(phrases, 1):
        print(f"{i}. {p}")
    print("\The supporting sentences :")
    for i, s in enumerate(supports, 1):
        print(f"{i}. {s}")
    print("\nUnified Generated Question:")
    print(unified_q)

    return {"phrases": phrases, "supports": supports, "question": unified_q}
unified_result = unified_question_from_top5_phrases(text_norm, ranked_blended, nlp, sbert, top_k=5)

السياق:
 يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان 

العبارات المختارة (Top):
1. الجهاز العصبي المركزي
2. الجهاز العصبي المحيطي
3. خلايا الدبق
4. بدءا من خلايا
5. غمد النخاعين في الجهاز

الجمل الداعمة:
1. يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
2. يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
3. يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
4. يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان
5. يتشكل غمد النخاعين في الجهاز العصبي المركزي بدءا من خلايا الدبق قليلة الاستطالات وفي الجهاز العصبي المحيطي من خلايا شوان

السؤال الموحد المولّد:
question: من أين يتكون غمد النخاعين؟
